- Try a simple DNN for classification prediction
- Use the 64f data at first
- Also try with/without standardizing the data (maybe for NN the results are different)

In [11]:
# !pip install tensorflow
# !pip install scikeras

In [12]:
import tensorflow as tf
print(tf. __version__)

2.10.1


In [13]:
# Neural networks

from tensorflow.keras.models import Sequential
from tensorflow.keras import layers
from tensorflow.keras.layers import Add, Input, Dense, Dropout, BatchNormalization, Embedding, Flatten, Concatenate, Reshape, Conv1D, AveragePooling1D, Multiply, MaxPool1D, Activation
from tensorflow.keras.regularizers import l1, l2
from scikeras.wrappers import KerasClassifier
from tensorflow_addons.layers import WeightNormalization

In [29]:
import pandas as pd 
import numpy as np
import sklearn
import pickle
import matplotlib.pyplot as plt
# import lazypredict
# import xgboost as xgb

# from skopt import BayesSearchCV
from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import ExtraTreesClassifier, StackingClassifier, BaggingClassifier, GradientBoostingClassifier
from sklearn.svm import SVC
from sklearn.neighbors import KNeighborsClassifier
from sklearn.metrics import ConfusionMatrixDisplay, confusion_matrix, accuracy_score
from sklearn.model_selection import train_test_split, GridSearchCV, KFold, RandomizedSearchCV, cross_val_score

# import optuna
# from lazypredict.Supervised import LazyClassifier
# import lightgbm as lgb
# from catboost import CatBoostClassifier

# from pytorch_tabnet.tab_model import TabNetClassifier
# import torch

In [15]:
def make_submission(preds):
    assert len(preds) == 5000
    
    # Read labels
    with open('test_labels_sorted.npy', 'rb') as f:
        test_labels = np.load(f)
    len(test_labels)
    
    submission = pd.DataFrame(columns=['id', 'class'])
    for label, pred in zip(test_labels, preds):
        submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
    return submission

In [16]:
def plot_confusion_matrix(y_val_from_train, y_pred_from_train):
    fig, ax = plt.subplots(figsize=(8, 5))
    cmp = ConfusionMatrixDisplay(confusion_matrix(y_val_from_train, y_pred_from_train))
    cmp.plot(ax=ax)
    plt.show();

In [17]:
# Load X_train
with open('X_train_75_std.npy', 'rb') as f:
    X_train = np.load(f)
print(X_train.shape)
X_train

(9000, 75)


array([[ 0.66868409,  0.16353656,  0.63277468, ..., -0.68600237,
        -0.75071056, -0.6719989 ],
       [ 0.37202545,  0.27579237,  0.65904756, ...,  0.06479231,
        -0.48439794,  0.56611352],
       [-1.67047552, -1.2187742 , -2.37040642, ..., -0.65838631,
        -0.38095167, -0.1542973 ],
       ...,
       [-0.24270722, -0.14209669, -0.32285351, ...,  0.37591901,
        -0.37936549,  0.58761686],
       [ 0.38630325,  0.31266521,  0.37767149, ...,  0.83458681,
         0.3138927 ,  0.79569199],
       [ 0.33077964, -0.0822815 , -0.51143673, ..., -1.1650511 ,
        -0.410986  ,  0.44873132]])

In [18]:
# Load y_train
with open('y_train.npy', 'rb') as f:
    y_train = np.load(f)
print(y_train.shape)
y_train

(9000,)


array([ 7, 13,  6, ...,  3,  3, 18], dtype=int64)

In [19]:
# Load X_test
with open('X_test_75_std.npy', 'rb') as f:
    X_test = np.load(f)
print(X_test.shape)
X_test

(5000, 75)


array([[-0.59806336,  0.6264903 , -0.15256881, ...,  1.17376188,
         0.23880484,  0.48877589],
       [-0.47352949,  0.94441404, -0.23499654, ..., -0.41222519,
        -0.40989637, -0.65814035],
       [-0.64168924, -1.56209892, -1.06875674, ...,  0.3385773 ,
        -0.56342902,  0.74796695],
       ...,
       [ 1.00103725, -0.3371114 ,  0.37115316, ..., -1.16055904,
        -0.46010399, -0.62722221],
       [-0.98752639, -1.20156778, -1.41423994, ..., -0.81406819,
        -0.78249592,  1.12406601],
       [-0.21177287, -0.85742305, -0.54931118, ...,  0.02750228,
        -0.76809252, -1.25225668]])

## Make small changes to y_train

In [20]:
y_train -= 1

In [21]:
y_train = tf.keras.utils.to_categorical(y_train, num_classes=20)

In [22]:
print(y_train.shape)

(9000, 20)


## Let's Standard Scale X_train and X_test

In [127]:
# from sklearn.preprocessing import StandardScaler
# scaler = StandardScaler()

In [128]:
# print(X_train)
# print()
# X_train = scaler.fit_transform(X_train)
# print(X_train)

[[-8.81665000e-01  1.04447100e+00  1.59010940e-01 ...  7.64136797e-02
   2.23461397e-02  1.29471645e+01]
 [-1.10552300e+00  1.12647200e+00  1.74547752e-01 ...  1.13979068e-01
   2.85805084e-02  1.38184886e+01]
 [-2.64679000e+00  3.47160000e-02 -1.61696002e+00 ...  7.77954261e-02
   3.10021816e-02  1.33114980e+01]
 ...
 [-1.56939900e+00  8.21211000e-01 -4.06112460e-01 ...  1.29546035e-01
   3.10393141e-02  1.38336216e+01]
 [-1.09474900e+00  1.15340700e+00  8.15228667e-03 ...  1.52495097e-01
   4.72684630e-02  1.39800549e+01]
 [-1.13664700e+00  8.64905000e-01 -5.17633651e-01 ...  5.24448737e-02
   3.02990790e-02  1.37358806e+01]]

[[ 0.66868409  0.16353656  0.63277468 ... -0.68600237 -0.75071056
  -0.6719989 ]
 [ 0.37202545  0.27579237  0.65904756 ...  0.06479231 -0.48439794
   0.56611352]
 [-1.67047552 -1.2187742  -2.37040642 ... -0.65838631 -0.38095167
  -0.1542973 ]
 ...
 [-0.24270722 -0.14209669 -0.32285351 ...  0.37591901 -0.37936549
   0.58761686]
 [ 0.38630325  0.31266521  0.37767

In [129]:
# print(X_test)
# print()
# X_test = scaler.transform(X_test)
# print(X_test)

[[-1.83755000e+00  1.38265100e+00 -3.05412347e-01 ...  1.69465441e-01
   4.55106589e-02  1.37640621e+01]
 [-1.74357700e+00  1.61488900e+00 -3.54157081e-01 ...  9.01118934e-02
   3.03245873e-02  1.29569175e+01]
 [-1.87047000e+00 -2.16077000e-01 -8.47212227e-01 ...  1.27677673e-01
   2.67303936e-02  1.39464683e+01]
 ...
 [-6.30872000e-01  6.78756000e-01  4.29758667e-03 ...  5.26696304e-02
   2.91492287e-02  1.29786762e+01]
 [-2.13143800e+00  4.72850000e-02 -1.05151830e+00 ...  7.00060125e-02
   2.16020454e-02  1.42111488e+01]
 [-1.54605600e+00  2.98677000e-01 -5.40031205e-01 ...  1.12113293e-01
   2.19392284e-02  1.25388069e+01]]

[[-0.59806336  0.6264903  -0.15256881 ...  1.17376188  0.23880484
   0.48877589]
 [-0.47352949  0.94441404 -0.23499654 ... -0.41222519 -0.40989637
  -0.65814035]
 [-0.64168924 -1.56209892 -1.06875674 ...  0.3385773  -0.56342902
   0.74796695]
 ...
 [ 1.00103725 -0.3371114   0.37115316 ... -1.16055904 -0.46010399
  -0.62722221]
 [-0.98752639 -1.20156778 -1.41423

In [130]:
# # Save X_train
# with open('X_train_75_std.npy', 'wb') as f:
#     np.save(f, X_train)
    
# with open('X_test_75_std.npy', 'wb') as f:
#     np.save(f, X_test)

## Let's build a Simple DNN

In [131]:
from tensorflow.python.client import device_lib
str(device_lib.list_local_devices())

'[name: "/device:CPU:0"\ndevice_type: "CPU"\nmemory_limit: 268435456\nlocality {\n}\nincarnation: 11894840068982339890\nxla_global_id: -1\n, name: "/device:GPU:0"\ndevice_type: "GPU"\nmemory_limit: 22712156160\nlocality {\n  bus_id: 1\n  links {\n  }\n}\nincarnation: 9297819330062516997\nphysical_device_desc: "device: 0, name: NVIDIA GeForce RTX 3090, pci bus id: 0000:01:00.0, compute capability: 8.6"\nxla_global_id: 416903419\n]'

In [13]:
# define baseline model
def baseline_model(input_dim=64, output_dim=20):
    # create model
    model = Sequential()
    model.add(Dense(8, input_dim=input_dim, activation='relu'))
    model.add(Dense(output_dim, activation='softmax'))
    # Compile model
    model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])
    return model

In [14]:
estimator = KerasClassifier(build_fn=baseline_model, epochs=200, batch_size=20, verbose=0)

In [36]:
kfold = KFold(n_splits=10, shuffle=True)

In [37]:
results = cross_val_score(estimator, X_train, y_train, cv=kfold)

C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:301: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  warnings.warn(
C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:301: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  warnings.warn(
C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:301: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  warnings.warn(
C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:301: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  warnings.warn(
C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:30

In [38]:
print("Baseline: %.2f%% (%.2f%%)" % (results.mean()*100, results.std()*100))

Baseline: 34.48% (22.01%)


# Let's build one NN - depth 10 - 89.7% +- 1.15%

In [ ]:
# TODO: Change this code

In [13]:
def create_neural_network(input_shape=64, depth=10, output_dim=20, batch_mod=2, num_neurons=250, drop_rate=0.1, learn_rate=.001,
                      r1_weight=0.02, r2_weight=0.02):
    '''A neural network architecture built using keras functional API'''
    act_reg = l1(r2_weight)
    kern_reg = l1(r1_weight)
    
    inputs = Input(shape=(input_shape,))
    batch1 = BatchNormalization()(inputs)
    hidden1 = Dense(num_neurons, activation='relu', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(batch1)
    dropout1 = Dropout(drop_rate)(hidden1)
    hidden2 = Dense(int(num_neurons/2), activation='relu', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(dropout1)
    
    skip_list = [batch1]
    last_layer_in_loop = hidden2
    
    for i in range(depth):
        added_layer = Concatenate()(skip_list + [last_layer_in_loop])
        skip_list.append(added_layer)
        b1 = None
        #Apply batch only on every i % N layers
        if i % batch_mod == 2:
            b1 = BatchNormalization()(added_layer)
        else:
            b1 = added_layer
        
        h1 = Dense(num_neurons, activation='relu', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(b1)
        d1 = Dropout(drop_rate)(h1)
        h2 = Dense(int(num_neurons/2), activation='relu', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(d1)
        d2 = Dropout(drop_rate)(h2)
        h3 =  Dense(int(num_neurons/2), activation='relu', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(d2)
        d3 = Dropout(drop_rate)(h3)
        h4 =  Dense(int(num_neurons/2), activation='relu', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(d3)
        last_layer_in_loop = h4
        c1 = Concatenate()(skip_list + [last_layer_in_loop])
        output = Dense(output_dim, activation='softmax')(c1)
    
    model = tf.keras.Model(inputs=inputs, outputs=output)
    model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])
    return model

In [67]:
estimator = KerasClassifier(build_fn=create_neural_network, epochs=200, batch_size=20, verbose=0)

In [68]:
kfold = KFold(n_splits=10, shuffle=True)

In [69]:
results = cross_val_score(estimator, X_train, y_train, cv=kfold)

C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:301: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  warnings.warn(
C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:301: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  warnings.warn(
C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:301: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  warnings.warn(
C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:301: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  warnings.warn(
C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:30

In [70]:
print("Baseline: %.2f%% (%.2f%%)" % (results.mean()*100, results.std()*100))

Baseline: 89.70% (1.15%)


# Let's train 3 more NN: Depth 12, 8, 6

## Depth 12 - 86.1%

In [26]:
def create_neural_network_12(input_shape=64, depth=12, output_dim=20, batch_mod=2, num_neurons=250, drop_rate=0.1, learn_rate=.001,
                      r1_weight=0.02, r2_weight=0.02):
    '''A neural network architecture built using keras functional API'''
    act_reg = l1(r2_weight)
    kern_reg = l1(r1_weight)
    
    inputs = Input(shape=(input_shape,))
    batch1 = BatchNormalization()(inputs)
    hidden1 = Dense(num_neurons, activation='relu', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(batch1)
    dropout1 = Dropout(drop_rate)(hidden1)
    hidden2 = Dense(int(num_neurons/2), activation='relu', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(dropout1)
    
    skip_list = [batch1]
    last_layer_in_loop = hidden2
    
    for i in range(depth):
        added_layer = Concatenate()(skip_list + [last_layer_in_loop])
        skip_list.append(added_layer)
        b1 = None
        #Apply batch only on every i % N layers
        if i % batch_mod == 2:
            b1 = BatchNormalization()(added_layer)
        else:
            b1 = added_layer
        
        h1 = Dense(num_neurons, activation='relu', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(b1)
        d1 = Dropout(drop_rate)(h1)
        h2 = Dense(int(num_neurons/2), activation='relu', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(d1)
        d2 = Dropout(drop_rate)(h2)
        h3 =  Dense(int(num_neurons/2), activation='relu', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(d2)
        d3 = Dropout(drop_rate)(h3)
        h4 =  Dense(int(num_neurons/2), activation='relu', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(d3)
        last_layer_in_loop = h4
        c1 = Concatenate()(skip_list + [last_layer_in_loop])
        output = Dense(output_dim, activation='softmax')(c1)
    
    model = tf.keras.Model(inputs=inputs, outputs=output)
    model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])
    return model

In [27]:
estimator_12 = KerasClassifier(build_fn=create_neural_network_12, epochs=200, batch_size=20, verbose=0)

In [28]:
kfold = KFold(n_splits=10, shuffle=True)

In [29]:
results = cross_val_score(estimator_12, X_train, y_train, cv=kfold)

C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:301: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  warnings.warn(
C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:301: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  warnings.warn(
C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:301: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  warnings.warn(
C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:301: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  warnings.warn(
C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:30

In [35]:
results.mean()

0.8612222222222222

## Depth 8 - 91.36% +- 0.42%

In [18]:
def create_neural_network_8(input_shape=64, depth=8, output_dim=20, batch_mod=2, num_neurons=250, drop_rate=0.1, learn_rate=.001,
                      r1_weight=0.02, r2_weight=0.02):
    '''A neural network architecture built using keras functional API'''
    act_reg = l1(r2_weight)
    kern_reg = l1(r1_weight)
    
    inputs = Input(shape=(input_shape,))
    batch1 = BatchNormalization()(inputs)
    hidden1 = Dense(num_neurons, activation='relu', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(batch1)
    dropout1 = Dropout(drop_rate)(hidden1)
    hidden2 = Dense(int(num_neurons/2), activation='relu', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(dropout1)
    
    skip_list = [batch1]
    last_layer_in_loop = hidden2
    
    for i in range(depth):
        added_layer = Concatenate()(skip_list + [last_layer_in_loop])
        skip_list.append(added_layer)
        b1 = None
        #Apply batch only on every i % N layers
        if i % batch_mod == 2:
            b1 = BatchNormalization()(added_layer)
        else:
            b1 = added_layer
        
        h1 = Dense(num_neurons, activation='relu', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(b1)
        d1 = Dropout(drop_rate)(h1)
        h2 = Dense(int(num_neurons/2), activation='relu', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(d1)
        d2 = Dropout(drop_rate)(h2)
        h3 =  Dense(int(num_neurons/2), activation='relu', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(d2)
        d3 = Dropout(drop_rate)(h3)
        h4 =  Dense(int(num_neurons/2), activation='relu', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(d3)
        last_layer_in_loop = h4
        c1 = Concatenate()(skip_list + [last_layer_in_loop])
        output = Dense(output_dim, activation='softmax')(c1)
    
    model = tf.keras.Model(inputs=inputs, outputs=output)
    model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])
    return model

In [19]:
estimator_8 = KerasClassifier(build_fn=create_neural_network_8, epochs=200, batch_size=20, verbose=0)

In [20]:
kfold = KFold(n_splits=5, shuffle=True)

In [21]:
results = cross_val_score(estimator_15, X_train, y_train, cv=kfold)

C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:301: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  warnings.warn(
C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:301: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  warnings.warn(
C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:301: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  warnings.warn(
C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:301: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  warnings.warn(
C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:30

In [22]:
print(results.mean())

0.9135555555555556


In [23]:
print("Baseline: %.2f%% (%.2f%%)" % (results.mean()*100, results.std()*100))

Baseline: 91.36% (0.42%)


## Depth 6 - 91.92% +- 0.44%

In [15]:
def create_neural_network_6(input_shape=64, depth=6, output_dim=20, batch_mod=2, num_neurons=250, drop_rate=0.1, learn_rate=.001,
                      r1_weight=0.02, r2_weight=0.02):
    '''A neural network architecture built using keras functional API'''
    act_reg = l1(r2_weight)
    kern_reg = l1(r1_weight)
    
    inputs = Input(shape=(input_shape,))
    batch1 = BatchNormalization()(inputs)
    hidden1 = Dense(num_neurons, activation='relu', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(batch1)
    dropout1 = Dropout(drop_rate)(hidden1)
    hidden2 = Dense(int(num_neurons/2), activation='relu', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(dropout1)
    
    skip_list = [batch1]
    last_layer_in_loop = hidden2
    
    for i in range(depth):
        added_layer = Concatenate()(skip_list + [last_layer_in_loop])
        skip_list.append(added_layer)
        b1 = None
        #Apply batch only on every i % N layers
        if i % batch_mod == 2:
            b1 = BatchNormalization()(added_layer)
        else:
            b1 = added_layer
        
        h1 = Dense(num_neurons, activation='relu', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(b1)
        d1 = Dropout(drop_rate)(h1)
        h2 = Dense(int(num_neurons/2), activation='relu', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(d1)
        d2 = Dropout(drop_rate)(h2)
        h3 =  Dense(int(num_neurons/2), activation='relu', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(d2)
        d3 = Dropout(drop_rate)(h3)
        h4 =  Dense(int(num_neurons/2), activation='relu', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(d3)
        last_layer_in_loop = h4
        c1 = Concatenate()(skip_list + [last_layer_in_loop])
        output = Dense(output_dim, activation='softmax')(c1)
    
    model = tf.keras.Model(inputs=inputs, outputs=output)
    model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])
    return model

In [16]:
estimator_6 = KerasClassifier(build_fn=create_neural_network_6, epochs=200, batch_size=20, verbose=0)

In [17]:
kfold = KFold(n_splits=5, shuffle=True)

In [18]:
results = cross_val_score(estimator_6, X_train, y_train, cv=kfold)

C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:301: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  warnings.warn(
C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:301: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  warnings.warn(
C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:301: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  warnings.warn(
C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:301: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  warnings.warn(
C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:30

In [19]:
print("Baseline: %.2f%% (%.2f%%)" % (results.mean()*100, results.std()*100))

Baseline: 91.92% (0.44%)


## Depth 4 - 92.5% +- 0.37%

In [13]:
def create_neural_network_4(input_shape=64, depth=4, output_dim=20, batch_mod=2, num_neurons=250, drop_rate=0.1, learn_rate=.001,
                      r1_weight=0.02, r2_weight=0.02):
    '''A neural network architecture built using keras functional API'''
    act_reg = l1(r2_weight)
    kern_reg = l1(r1_weight)
    
    inputs = Input(shape=(input_shape,))
    batch1 = BatchNormalization()(inputs)
    hidden1 = Dense(num_neurons, activation='relu', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(batch1)
    dropout1 = Dropout(drop_rate)(hidden1)
    hidden2 = Dense(int(num_neurons/2), activation='relu', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(dropout1)
    
    skip_list = [batch1]
    last_layer_in_loop = hidden2
    
    for i in range(depth):
        added_layer = Concatenate()(skip_list + [last_layer_in_loop])
        skip_list.append(added_layer)
        b1 = None
        #Apply batch only on every i % N layers
        if i % batch_mod == 2:
            b1 = BatchNormalization()(added_layer)
        else:
            b1 = added_layer
        
        h1 = Dense(num_neurons, activation='relu', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(b1)
        d1 = Dropout(drop_rate)(h1)
        h2 = Dense(int(num_neurons/2), activation='relu', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(d1)
        d2 = Dropout(drop_rate)(h2)
        h3 =  Dense(int(num_neurons/2), activation='relu', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(d2)
        d3 = Dropout(drop_rate)(h3)
        h4 =  Dense(int(num_neurons/2), activation='relu', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(d3)
        last_layer_in_loop = h4
        c1 = Concatenate()(skip_list + [last_layer_in_loop])
        output = Dense(output_dim, activation='softmax')(c1)
    
    model = tf.keras.Model(inputs=inputs, outputs=output)
    model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])
    return model

In [14]:
estimator_4 = KerasClassifier(build_fn=create_neural_network_4, epochs=200, batch_size=20, verbose=0)

In [15]:
kfold = KFold(n_splits=5, shuffle=True)

In [16]:
%%time
results = cross_val_score(estimator_4, X_train, y_train, cv=kfold)

C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:301: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  warnings.warn(
C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:301: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  warnings.warn(
C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:301: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  warnings.warn(
C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:301: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  warnings.warn(
C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:30

CPU times: total: 5min 28s
Wall time: 29min 24s


In [17]:
print("Baseline: %.2f%% (%.2f%%)" % (results.mean()*100, results.std()*100))

Baseline: 92.50% (0.37%)


### Fit depth=4 model, let's get some results and predictions

## Depth 5 - 

In [62]:
def create_neural_network_5(input_shape=64, depth=5, output_dim=20, batch_mod=2, num_neurons=250, drop_rate=0.1, learn_rate=.001,
                      r1_weight=0.02, r2_weight=0.02):
    '''A neural network architecture built using keras functional API'''
    act_reg = l1(r2_weight)
    kern_reg = l1(r1_weight)
    
    inputs = Input(shape=(input_shape,))
    batch1 = BatchNormalization()(inputs)
    hidden1 = Dense(num_neurons, activation='relu', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(batch1)
    dropout1 = Dropout(drop_rate)(hidden1)
    hidden2 = Dense(int(num_neurons/2), activation='relu', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(dropout1)
    
    skip_list = [batch1]
    last_layer_in_loop = hidden2
    
    for i in range(depth):
        added_layer = Concatenate()(skip_list + [last_layer_in_loop])
        skip_list.append(added_layer)
        b1 = None
        #Apply batch only on every i % N layers
        if i % batch_mod == 2:
            b1 = BatchNormalization()(added_layer)
        else:
            b1 = added_layer
        
        h1 = Dense(num_neurons, activation='relu', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(b1)
        d1 = Dropout(drop_rate)(h1)
        h2 = Dense(int(num_neurons/2), activation='relu', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(d1)
        d2 = Dropout(drop_rate)(h2)
        h3 =  Dense(int(num_neurons/2), activation='relu', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(d2)
        d3 = Dropout(drop_rate)(h3)
        h4 =  Dense(int(num_neurons/2), activation='relu', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(d3)
        last_layer_in_loop = h4
        c1 = Concatenate()(skip_list + [last_layer_in_loop])
        output = Dense(output_dim, activation='softmax')(c1)
    
    model = tf.keras.Model(inputs=inputs, outputs=output)
    model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])
    return model

### Epochs: 500, BS: 50 - 93.64% +- 0.66% -> On Kaggle: 87.7-87.9%

In [14]:
estimator_5 = KerasClassifier(build_fn=create_neural_network_5, epochs=500, batch_size=50, verbose=0)

In [15]:
kfold = KFold(n_splits=5, shuffle=True)

In [16]:
%%time
results = cross_val_score(estimator_5, X_train, y_train, cv=kfold)

C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:301: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  warnings.warn(
C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:301: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  warnings.warn(
C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:301: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  warnings.warn(
C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:301: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  warnings.warn(
C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:30

CPU times: total: 6min 11s
Wall time: 36min 14s


In [17]:
print("Baseline: %.2f%% (%.2f%%)" % (results.mean()*100, results.std()*100))

Baseline: 93.64% (0.66%)


### Epochs 5000, BS: 200 - 94.06% +- 0.44%

In [15]:
estimator_5 = KerasClassifier(build_fn=create_neural_network_5, epochs=5000, batch_size=200, verbose=0)

In [16]:
kfold = KFold(n_splits=5, shuffle=True)

In [17]:
%%time
results = cross_val_score(estimator_5, X_train, y_train, cv=kfold)

C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:301: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  warnings.warn(
C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:301: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  warnings.warn(
C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:301: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  warnings.warn(
C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:301: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  warnings.warn(
C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:30

CPU times: total: 17min 4s
Wall time: 1h 34min 20s


In [18]:
print("Baseline: %.2f%% (%.2f%%)" % (results.mean()*100, results.std()*100))

Baseline: 94.06% (0.44%)


### TODO: I have to fit the model on all of the data then save it. 

In [64]:
estimator_5 = KerasClassifier(build_fn=create_neural_network_5)
estimator_5.fit(X_train, y_train, epochs=300, batch_size=256, validation_split=0.05)

Epoch 1/300


C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:301: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  warnings.warn(


34/34 [==============================] - 2s 20ms/step - loss: 877.1902 - accuracy: 0.7701 - val_loss: 479.0240 - val_accuracy: 0.8356
Epoch 2/300
34/34 [==============================] - 0s 10ms/step - loss: 304.9274 - accuracy: 0.8800 - val_loss: 168.8110 - val_accuracy: 0.8622
Epoch 3/300
34/34 [==============================] - 0s 10ms/step - loss: 102.8011 - accuracy: 0.8903 - val_loss: 49.6376 - val_accuracy: 0.8644
Epoch 4/300
34/34 [==============================] - 0s 10ms/step - loss: 26.3655 - accuracy: 0.8950 - val_loss: 10.7526 - val_accuracy: 0.8622
Epoch 5/300
34/34 [==============================] - 0s 10ms/step - loss: 6.8666 - accuracy: 0.9018 - val_loss: 5.2439 - val_accuracy: 0.8867
Epoch 6/300
34/34 [==============================] - 0s 10ms/step - loss: 4.9669 - accuracy: 0.9036 - val_loss: 4.8746 - val_accuracy: 0.8778
Epoch 7/300
34/34 [==============================] - 0s 10ms/step - loss: 4.8286 - accuracy: 0.9083 - val_loss: 4.8434 - val_accuracy: 0.8844
Epoch

34/34 [==============================] - 0s 10ms/step - loss: 4.6704 - accuracy: 0.9457 - val_loss: 4.7386 - val_accuracy: 0.9333
Epoch 116/300
34/34 [==============================] - 0s 10ms/step - loss: 4.6665 - accuracy: 0.9513 - val_loss: 4.7330 - val_accuracy: 0.9311
Epoch 117/300
34/34 [==============================] - 0s 10ms/step - loss: 4.6739 - accuracy: 0.9454 - val_loss: 4.7335 - val_accuracy: 0.9333
Epoch 118/300
34/34 [==============================] - 0s 9ms/step - loss: 4.6620 - accuracy: 0.9510 - val_loss: 4.7045 - val_accuracy: 0.9333
Epoch 119/300
34/34 [==============================] - 0s 10ms/step - loss: 4.6787 - accuracy: 0.9451 - val_loss: 4.7045 - val_accuracy: 0.9356
Epoch 120/300
34/34 [==============================] - 0s 10ms/step - loss: 4.6683 - accuracy: 0.9482 - val_loss: 4.6936 - val_accuracy: 0.9489
Epoch 121/300
34/34 [==============================] - 0s 10ms/step - loss: 4.6589 - accuracy: 0.9508 - val_loss: 4.6908 - val_accuracy: 0.9422
Epoch 1

34/34 [==============================] - 0s 10ms/step - loss: 4.6527 - accuracy: 0.9527 - val_loss: 4.7073 - val_accuracy: 0.9378
Epoch 173/300
34/34 [==============================] - 0s 10ms/step - loss: 4.6608 - accuracy: 0.9504 - val_loss: 4.6980 - val_accuracy: 0.9378
Epoch 174/300
34/34 [==============================] - 0s 10ms/step - loss: 4.6666 - accuracy: 0.9485 - val_loss: 4.7029 - val_accuracy: 0.9356
Epoch 175/300
34/34 [==============================] - 0s 10ms/step - loss: 4.6585 - accuracy: 0.9511 - val_loss: 4.6978 - val_accuracy: 0.9333
Epoch 176/300
34/34 [==============================] - 0s 10ms/step - loss: 4.6661 - accuracy: 0.9483 - val_loss: 4.7121 - val_accuracy: 0.9400
Epoch 177/300
34/34 [==============================] - 0s 9ms/step - loss: 4.6640 - accuracy: 0.9513 - val_loss: 4.7269 - val_accuracy: 0.9400
Epoch 178/300
34/34 [==============================] - 0s 9ms/step - loss: 4.6520 - accuracy: 0.9522 - val_loss: 4.7012 - val_accuracy: 0.9422
Epoch 17

34/34 [==============================] - 0s 10ms/step - loss: 4.6466 - accuracy: 0.9539 - val_loss: 4.7252 - val_accuracy: 0.9311
Epoch 287/300
34/34 [==============================] - 0s 9ms/step - loss: 4.6468 - accuracy: 0.9539 - val_loss: 4.7242 - val_accuracy: 0.9244
Epoch 288/300
34/34 [==============================] - 0s 10ms/step - loss: 4.6502 - accuracy: 0.9543 - val_loss: 4.7168 - val_accuracy: 0.9378
Epoch 289/300
34/34 [==============================] - 0s 10ms/step - loss: 4.6423 - accuracy: 0.9564 - val_loss: 4.7175 - val_accuracy: 0.9333
Epoch 290/300
34/34 [==============================] - 0s 9ms/step - loss: 4.6505 - accuracy: 0.9532 - val_loss: 4.7294 - val_accuracy: 0.9289
Epoch 291/300
34/34 [==============================] - 0s 9ms/step - loss: 4.6548 - accuracy: 0.9520 - val_loss: 4.7187 - val_accuracy: 0.9400
Epoch 292/300
34/34 [==============================] - 0s 10ms/step - loss: 4.6507 - accuracy: 0.9540 - val_loss: 4.6986 - val_accuracy: 0.9311
Epoch 293

KerasClassifier(
	model=None
	build_fn=<function create_neural_network_5 at 0x0000017C4AAB8940>
	warm_start=False
	random_state=None
	optimizer=rmsprop
	loss=None
	metrics=None
	batch_size=None
	validation_batch_size=None
	verbose=1
	callbacks=None
	validation_split=0.0
	shuffle=True
	run_eagerly=False
	epochs=1
	class_weight=None
)

In [29]:
preds = estimator_5.predict(X_test)
preds

157/157 [==============================] - 1s 3ms/step


array([[0, 0, 1, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       ...,
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [1, 0, 0, ..., 0, 0, 0]])

In [30]:
preds.shape

(5000, 20)

In [31]:
preds_as_array = np.argmax(preds, axis=1)
preds_as_array += 1
preds_as_array

array([3, 4, 5, ..., 4, 5, 1], dtype=int64)

In [32]:
print(min(preds_as_array), max(preds_as_array))

1 20


In [33]:
sub = make_submission(preds_as_array)
sub

C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from p

C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from p

C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from p

C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from p

C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from p

C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from p

id class
0     10001     3
1     10002     4
2     10004     5
3     10008    20
4     10009    17
...     ...   ...
4995  23986     9
4996  23991    12
4997  23992     4
4998  23998     5
4999  24000     1

[5000 rows x 2 columns]

In [34]:
sub.to_csv('submission_keras_5depth_100e_50bs_baseline_64f.csv', index=False)

## Depth 3 - 

In [71]:
from keras.callbacks import LearningRateScheduler

def decay_schedule(epoch: int, lr: float):
    if (epoch % 5 == 0) and (epoch != 0):
        lr = lr * 0.1
    return lr

In [99]:
def create_neural_network_3(input_shape=64, depth=3, output_dim=20, batch_mod=2, num_neurons=250, drop_rate=0.1,
                      r1_weight=0.02, r2_weight=0.02):
    '''A neural network architecture built using keras functional API'''
    act_reg = l1(r2_weight)
    kern_reg = l1(r1_weight)
    
    inputs = Input(shape=(input_shape,))
    batch1 = BatchNormalization()(inputs)
    hidden1 = Dense(num_neurons, activation='relu', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(batch1)
    dropout1 = Dropout(drop_rate)(hidden1)
    hidden2 = Dense(int(num_neurons/2), activation='relu', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(dropout1)
    
    skip_list = [batch1]
    last_layer_in_loop = hidden2
    
    for i in range(depth):
        added_layer = Concatenate()(skip_list + [last_layer_in_loop])
        skip_list.append(added_layer)
        b1 = None
        #Apply batch only on every i % N layers
        if i % batch_mod == 2:
            b1 = BatchNormalization()(added_layer)
        else:
            b1 = added_layer
        
        h1 = Dense(num_neurons, activation='relu', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(b1)
        d1 = Dropout(drop_rate)(h1)
        h2 = Dense(int(num_neurons/2), activation='relu', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(d1)
        d2 = Dropout(drop_rate)(h2)
        h3 =  Dense(int(num_neurons/2), activation='relu', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(d2)
        d3 = Dropout(drop_rate)(h3)
        h4 =  Dense(int(num_neurons/2), activation='relu', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(d3)
        last_layer_in_loop = h4
        c1 = Concatenate()(skip_list + [last_layer_in_loop])
        output = Dense(output_dim, activation='softmax')(c1)
    
    model = tf.keras.Model(inputs=inputs, outputs=output)
    model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])
    return model

In [38]:
estimator_3 = KerasClassifier(build_fn=create_neural_network_3, epochs=500, batch_size=50, verbose=0)

In [39]:
kfold = KFold(n_splits=5, shuffle=True)

In [40]:
%%time
results = cross_val_score(estimator_3, X_train, y_train, cv=kfold)

C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:301: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  warnings.warn(
C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:301: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  warnings.warn(
C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:301: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  warnings.warn(
C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:301: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  warnings.warn(
C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:30

CPU times: total: 4min 16s
Wall time: 24min 44s


In [41]:
print("Baseline: %.2f%% (%.2f%%)" % (results.mean()*100, results.std()*100))

Baseline: 93.66% (0.39%)


In [69]:
lr_scheduler = LearningRateScheduler(decay_schedule)
estimator_3 = KerasClassifier(build_fn=create_neural_network_3)
estimator_3.fit(X_train, y_train, validation_split=0.05, epochs=300, batch_size=128, callbacks=[lr_scheduler])

Epoch 1/300


C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:301: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  warnings.warn(


67/67 [==============================] - 2s 11ms/step - loss: 335.9474 - accuracy: 0.7174 - val_loss: 116.9806 - val_accuracy: 0.8222
Epoch 2/300
67/67 [==============================] - 0s 6ms/step - loss: 43.3488 - accuracy: 0.8618 - val_loss: 6.2139 - val_accuracy: 0.8378
Epoch 3/300
67/67 [==============================] - 0s 6ms/step - loss: 2.6579 - accuracy: 0.8770 - val_loss: 1.8848 - val_accuracy: 0.8533
Epoch 4/300
67/67 [==============================] - 0s 6ms/step - loss: 1.8131 - accuracy: 0.8855 - val_loss: 1.8189 - val_accuracy: 0.8733
Epoch 5/300
67/67 [==============================] - 0s 7ms/step - loss: 1.7808 - accuracy: 0.8945 - val_loss: 1.8009 - val_accuracy: 0.8800
Epoch 6/300
67/67 [==============================] - 0s 7ms/step - loss: 1.7609 - accuracy: 0.8935 - val_loss: 1.7737 - val_accuracy: 0.8889
Epoch 7/300
67/67 [==============================] - 0s 6ms/step - loss: 1.7404 - accuracy: 0.8981 - val_loss: 1.7613 - val_accuracy: 0.8867
Epoch 8/300
67/67 [

Epoch 59/300
67/67 [==============================] - 0s 7ms/step - loss: 1.5828 - accuracy: 0.9422 - val_loss: 1.6189 - val_accuracy: 0.9222
Epoch 60/300
67/67 [==============================] - 0s 6ms/step - loss: 1.5933 - accuracy: 0.9382 - val_loss: 1.6034 - val_accuracy: 0.9378
Epoch 61/300
67/67 [==============================] - 0s 6ms/step - loss: 1.5879 - accuracy: 0.9388 - val_loss: 1.6119 - val_accuracy: 0.9356
Epoch 62/300
67/67 [==============================] - 0s 6ms/step - loss: 1.5863 - accuracy: 0.9436 - val_loss: 1.6135 - val_accuracy: 0.9311
Epoch 63/300
67/67 [==============================] - 0s 7ms/step - loss: 1.5863 - accuracy: 0.9399 - val_loss: 1.6124 - val_accuracy: 0.9311
Epoch 64/300
67/67 [==============================] - 0s 7ms/step - loss: 1.5894 - accuracy: 0.9391 - val_loss: 1.6117 - val_accuracy: 0.9400
Epoch 65/300
67/67 [==============================] - 0s 7ms/step - loss: 1.5896 - accuracy: 0.9391 - val_loss: 1.6010 - val_accuracy: 0.9422
Epoch 

67/67 [==============================] - 0s 6ms/step - loss: 1.5591 - accuracy: 0.9485 - val_loss: 1.5853 - val_accuracy: 0.9444
Epoch 174/300
67/67 [==============================] - 0s 7ms/step - loss: 1.5633 - accuracy: 0.9470 - val_loss: 1.5901 - val_accuracy: 0.9400
Epoch 175/300
67/67 [==============================] - 0s 7ms/step - loss: 1.5633 - accuracy: 0.9474 - val_loss: 1.5874 - val_accuracy: 0.9378
Epoch 176/300
67/67 [==============================] - 0s 7ms/step - loss: 1.5649 - accuracy: 0.9476 - val_loss: 1.5882 - val_accuracy: 0.9378
Epoch 177/300
67/67 [==============================] - 0s 6ms/step - loss: 1.5598 - accuracy: 0.9509 - val_loss: 1.5975 - val_accuracy: 0.9311
Epoch 178/300
67/67 [==============================] - 0s 7ms/step - loss: 1.5621 - accuracy: 0.9481 - val_loss: 1.5923 - val_accuracy: 0.9422
Epoch 179/300
67/67 [==============================] - 0s 7ms/step - loss: 1.5641 - accuracy: 0.9457 - val_loss: 1.5806 - val_accuracy: 0.9378
Epoch 180/300

67/67 [==============================] - 0s 6ms/step - loss: 1.5551 - accuracy: 0.9487 - val_loss: 1.5926 - val_accuracy: 0.9467
Epoch 288/300
67/67 [==============================] - 0s 6ms/step - loss: 1.5601 - accuracy: 0.9467 - val_loss: 1.5802 - val_accuracy: 0.9378
Epoch 289/300
67/67 [==============================] - 0s 6ms/step - loss: 1.5539 - accuracy: 0.9484 - val_loss: 1.5799 - val_accuracy: 0.9400
Epoch 290/300
67/67 [==============================] - 0s 7ms/step - loss: 1.5539 - accuracy: 0.9505 - val_loss: 1.5954 - val_accuracy: 0.9356
Epoch 291/300
67/67 [==============================] - 0s 6ms/step - loss: 1.5492 - accuracy: 0.9498 - val_loss: 1.5799 - val_accuracy: 0.9422
Epoch 292/300
67/67 [==============================] - 0s 6ms/step - loss: 1.5583 - accuracy: 0.9488 - val_loss: 1.5991 - val_accuracy: 0.9333
Epoch 293/300
67/67 [==============================] - 0s 7ms/step - loss: 1.5488 - accuracy: 0.9519 - val_loss: 1.5832 - val_accuracy: 0.9400
Epoch 294/300

KerasClassifier(
	model=None
	build_fn=<function create_neural_network_3 at 0x0000017C25D78550>
	warm_start=False
	random_state=None
	optimizer=rmsprop
	loss=None
	metrics=None
	batch_size=None
	validation_batch_size=None
	verbose=1
	callbacks=None
	validation_split=0.0
	shuffle=True
	run_eagerly=False
	epochs=1
	class_weight=None
)

In [70]:
preds = estimator_3.predict(X_test)
preds

157/157 [==============================] - 0s 2ms/step


array([[0, 0, 1, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       ...,
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [1, 0, 0, ..., 0, 0, 0]])

In [71]:
preds_as_array = np.argmax(preds, axis=1)
preds_as_array += 1
preds_as_array

array([3, 4, 5, ..., 4, 5, 1], dtype=int64)

In [72]:
sub = make_submission(preds_as_array)
sub

C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from p

C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from p

C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from p

C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from p

C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from p

C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from p

id class
0     10001     3
1     10002     4
2     10004     5
3     10008    20
4     10009    17
...     ...   ...
4995  23986    19
4996  23991    12
4997  23992     4
4998  23998     5
4999  24000     1

[5000 rows x 2 columns]

In [73]:
sub.to_csv('submission_keras_3depth_300e_128bs_wd_baseline_64f_std.csv', index=False)

## Depth 2

In [113]:
def create_neural_network_2(input_shape=64, depth=2, output_dim=20, batch_mod=2, num_neurons=250, drop_rate=0.1,
                      r1_weight=0.02, r2_weight=0.02):
    '''A neural network architecture built using keras functional API'''
    act_reg = l1(r2_weight)
    kern_reg = l1(r1_weight)
    
    inputs = Input(shape=(input_shape,))
    batch1 = BatchNormalization()(inputs)
    hidden1 = Dense(num_neurons, activation='sigmoid', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(batch1)
    dropout1 = Dropout(drop_rate)(hidden1)
    hidden2 = Dense(int(num_neurons/2), activation='sigmoid', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(dropout1)
    
    skip_list = [batch1]
    last_layer_in_loop = hidden2
    
    for i in range(depth):
        added_layer = Concatenate()(skip_list + [last_layer_in_loop])
        skip_list.append(added_layer)
        b1 = None
        #Apply batch only on every i % N layers
        if i % batch_mod == 2:
            b1 = BatchNormalization()(added_layer)
        else:
            b1 = added_layer
        
        h1 = Dense(num_neurons, activation='sigmoid', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(b1)
        d1 = Dropout(drop_rate)(h1)
        h2 = Dense(int(num_neurons/2), activation='sigmoid', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(d1)
        d2 = Dropout(drop_rate)(h2)
        h3 =  Dense(int(num_neurons/2), activation='sigmoid', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(d2)
        d3 = Dropout(drop_rate)(h3)
        h4 =  Dense(int(num_neurons/2), activation='sigmoid', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(d3)
        last_layer_in_loop = h4
        c1 = Concatenate()(skip_list + [last_layer_in_loop])
        output = Dense(output_dim, activation='softmax')(c1)
    
    model = tf.keras.Model(inputs=inputs, outputs=output)
    model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])
    return model

In [114]:
lr_scheduler = LearningRateScheduler(decay_schedule)
estimator_2 = KerasClassifier(build_fn=create_neural_network_2)
estimator_2.fit(X_train, y_train, validation_split=0.05, epochs=300, batch_size=128, callbacks=[lr_scheduler])

Epoch 1/300


C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:301: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  warnings.warn(


67/67 [==============================] - 1s 9ms/step - loss: 235.7116 - accuracy: 0.6065 - val_loss: 101.5404 - val_accuracy: 0.7933
Epoch 2/300
67/67 [==============================] - 0s 5ms/step - loss: 46.4396 - accuracy: 0.8373 - val_loss: 19.2159 - val_accuracy: 0.8156
Epoch 3/300
67/67 [==============================] - 0s 5ms/step - loss: 16.6387 - accuracy: 0.8584 - val_loss: 15.8664 - val_accuracy: 0.8511
Epoch 4/300
67/67 [==============================] - 0s 5ms/step - loss: 15.5335 - accuracy: 0.8779 - val_loss: 15.2825 - val_accuracy: 0.8600
Epoch 5/300
67/67 [==============================] - 0s 5ms/step - loss: 14.9822 - accuracy: 0.8846 - val_loss: 14.7370 - val_accuracy: 0.8800
Epoch 6/300
67/67 [==============================] - 0s 5ms/step - loss: 14.4305 - accuracy: 0.8935 - val_loss: 14.1616 - val_accuracy: 0.8800
Epoch 7/300
67/67 [==============================] - 0s 5ms/step - loss: 13.8541 - accuracy: 0.9005 - val_loss: 13.6237 - val_accuracy: 0.8889
Epoch 8/3

Epoch 116/300
67/67 [==============================] - 0s 5ms/step - loss: 1.1256 - accuracy: 0.9453 - val_loss: 1.1453 - val_accuracy: 0.9356
Epoch 117/300
67/67 [==============================] - 0s 5ms/step - loss: 1.1212 - accuracy: 0.9427 - val_loss: 1.1495 - val_accuracy: 0.9311
Epoch 118/300
67/67 [==============================] - 0s 5ms/step - loss: 1.1132 - accuracy: 0.9439 - val_loss: 1.1347 - val_accuracy: 0.9400
Epoch 119/300
67/67 [==============================] - 0s 5ms/step - loss: 1.1053 - accuracy: 0.9453 - val_loss: 1.1272 - val_accuracy: 0.9422
Epoch 120/300
67/67 [==============================] - 0s 5ms/step - loss: 1.0976 - accuracy: 0.9451 - val_loss: 1.1265 - val_accuracy: 0.9400
Epoch 121/300
67/67 [==============================] - 0s 5ms/step - loss: 1.0945 - accuracy: 0.9451 - val_loss: 1.1176 - val_accuracy: 0.9333
Epoch 122/300
67/67 [==============================] - 0s 5ms/step - loss: 1.0868 - accuracy: 0.9449 - val_loss: 1.1101 - val_accuracy: 0.9356

67/67 [==============================] - 0s 5ms/step - loss: 0.8294 - accuracy: 0.9513 - val_loss: 0.8574 - val_accuracy: 0.9467
Epoch 231/300
67/67 [==============================] - 0s 5ms/step - loss: 0.8351 - accuracy: 0.9487 - val_loss: 0.8669 - val_accuracy: 0.9400
Epoch 232/300
67/67 [==============================] - 0s 5ms/step - loss: 0.8327 - accuracy: 0.9465 - val_loss: 0.8756 - val_accuracy: 0.9356
Epoch 233/300
67/67 [==============================] - 0s 5ms/step - loss: 0.8367 - accuracy: 0.9467 - val_loss: 0.8610 - val_accuracy: 0.9422
Epoch 234/300
67/67 [==============================] - 0s 5ms/step - loss: 0.8371 - accuracy: 0.9492 - val_loss: 0.8658 - val_accuracy: 0.9378
Epoch 235/300
67/67 [==============================] - 0s 5ms/step - loss: 0.8325 - accuracy: 0.9481 - val_loss: 0.8591 - val_accuracy: 0.9378
Epoch 236/300
67/67 [==============================] - 0s 5ms/step - loss: 0.8337 - accuracy: 0.9483 - val_loss: 0.8642 - val_accuracy: 0.9356
Epoch 237/300

KerasClassifier(
	model=None
	build_fn=<function create_neural_network_2 at 0x0000017C760E9310>
	warm_start=False
	random_state=None
	optimizer=rmsprop
	loss=None
	metrics=None
	batch_size=None
	validation_batch_size=None
	verbose=1
	callbacks=None
	validation_split=0.0
	shuffle=True
	run_eagerly=False
	epochs=1
	class_weight=None
)

## Depth 1

In [24]:
def create_neural_network_1(input_shape=75, depth=1, output_dim=20, batch_mod=2, num_neurons=16, drop_rate=0.1,
                      r1_weight=0.02, r2_weight=0.02):
    '''A neural network architecture built using keras functional API'''
    act_reg = l1(r2_weight)
    kern_reg = l1(r1_weight)
    
    inputs = Input(shape=(input_shape,))
    batch1 = BatchNormalization()(inputs)
    hidden1 = Dense(num_neurons, activation='sigmoid', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(batch1)
    dropout1 = Dropout(drop_rate)(hidden1)
    hidden2 = Dense(int(num_neurons/2), activation='sigmoid', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(dropout1)
    
    skip_list = [batch1]
    last_layer_in_loop = hidden2
    
#     for i in range(depth):
    added_layer = Concatenate()(skip_list + [last_layer_in_loop])
    skip_list.append(added_layer)
#     b1 = None
    #Apply batch only on every i % N layers
#     if i % batch_mod == 2:
    b1 = BatchNormalization()(added_layer)
#     else:
#         b1 = added_layer

    h1 = Dense(num_neurons, activation='sigmoid', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(b1)
    d1 = Dropout(drop_rate)(h1)
    h2 = Dense(int(num_neurons/2), activation='sigmoid', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(d1)
    d2 = Dropout(drop_rate)(h2)
    h3 =  Dense(int(num_neurons/2), activation='sigmoid', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(d2)
    d3 = Dropout(drop_rate)(h3)
    h4 =  Dense(int(num_neurons/2), activation='sigmoid', kernel_regularizer=kern_reg, activity_regularizer=act_reg)(d3)
    last_layer_in_loop = h4
    c1 = Concatenate()(skip_list + [last_layer_in_loop])
    output = Dense(output_dim, activation='softmax')(c1)
    
    model = tf.keras.Model(inputs=inputs, outputs=output)
    model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])
    return model

- Adam, epochs 300, bs 128, val_loss=0.18
- Adamax, epochs 300, bs 128, val_loss=0.19

In [178]:
lr_scheduler = LearningRateScheduler(decay_schedule)
estimator_1 = KerasClassifier(build_fn=create_neural_network_1)
estimator_1.fit(X_train, y_train, validation_split=0.05, epochs=300, batch_size=128, callbacks=[lr_scheduler]) # val loss 0.1864

Epoch 1/300


C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:301: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  warnings.warn(


67/67 [==============================] - 1s 8ms/step - loss: 9.6729 - accuracy: 0.3118 - val_loss: 7.4928 - val_accuracy: 0.4933
Epoch 2/300
67/67 [==============================] - 0s 4ms/step - loss: 5.9038 - accuracy: 0.6089 - val_loss: 4.5408 - val_accuracy: 0.6556
Epoch 3/300
67/67 [==============================] - 0s 4ms/step - loss: 3.5501 - accuracy: 0.7340 - val_loss: 2.7819 - val_accuracy: 0.7333
Epoch 4/300
67/67 [==============================] - 0s 4ms/step - loss: 2.3145 - accuracy: 0.7853 - val_loss: 2.0510 - val_accuracy: 0.7622
Epoch 5/300
67/67 [==============================] - 0s 4ms/step - loss: 1.8313 - accuracy: 0.8110 - val_loss: 1.6991 - val_accuracy: 0.7933
Epoch 6/300
67/67 [==============================] - 0s 4ms/step - loss: 1.5266 - accuracy: 0.8250 - val_loss: 1.4380 - val_accuracy: 0.8089
Epoch 7/300
67/67 [==============================] - 0s 4ms/step - loss: 1.3091 - accuracy: 0.8361 - val_loss: 1.2664 - val_accuracy: 0.8156
Epoch 8/300
67/67 [======

Epoch 59/300
67/67 [==============================] - 0s 4ms/step - loss: 0.3087 - accuracy: 0.9215 - val_loss: 0.3234 - val_accuracy: 0.9156
Epoch 60/300
67/67 [==============================] - 0s 4ms/step - loss: 0.3038 - accuracy: 0.9204 - val_loss: 0.3205 - val_accuracy: 0.9178
Epoch 61/300
67/67 [==============================] - 0s 4ms/step - loss: 0.2968 - accuracy: 0.9213 - val_loss: 0.3182 - val_accuracy: 0.9178
Epoch 62/300
67/67 [==============================] - 0s 4ms/step - loss: 0.2943 - accuracy: 0.9219 - val_loss: 0.3116 - val_accuracy: 0.9222
Epoch 63/300
67/67 [==============================] - 0s 4ms/step - loss: 0.2947 - accuracy: 0.9216 - val_loss: 0.3094 - val_accuracy: 0.9200
Epoch 64/300
67/67 [==============================] - 0s 4ms/step - loss: 0.2942 - accuracy: 0.9198 - val_loss: 0.3078 - val_accuracy: 0.9178
Epoch 65/300
67/67 [==============================] - 0s 4ms/step - loss: 0.2889 - accuracy: 0.9240 - val_loss: 0.3042 - val_accuracy: 0.9222
Epoch 

67/67 [==============================] - 0s 4ms/step - loss: 0.1974 - accuracy: 0.9377 - val_loss: 0.2141 - val_accuracy: 0.9267
Epoch 174/300
67/67 [==============================] - 0s 4ms/step - loss: 0.1990 - accuracy: 0.9366 - val_loss: 0.2131 - val_accuracy: 0.9333
Epoch 175/300
67/67 [==============================] - 0s 4ms/step - loss: 0.1982 - accuracy: 0.9371 - val_loss: 0.2135 - val_accuracy: 0.9289
Epoch 176/300
67/67 [==============================] - 0s 4ms/step - loss: 0.1936 - accuracy: 0.9400 - val_loss: 0.2140 - val_accuracy: 0.9289
Epoch 177/300
67/67 [==============================] - 0s 4ms/step - loss: 0.1989 - accuracy: 0.9375 - val_loss: 0.2125 - val_accuracy: 0.9289
Epoch 178/300
67/67 [==============================] - 0s 4ms/step - loss: 0.1982 - accuracy: 0.9368 - val_loss: 0.2117 - val_accuracy: 0.9333
Epoch 179/300
67/67 [==============================] - 0s 4ms/step - loss: 0.1981 - accuracy: 0.9363 - val_loss: 0.2117 - val_accuracy: 0.9289
Epoch 180/300

67/67 [==============================] - 0s 4ms/step - loss: 0.1812 - accuracy: 0.9412 - val_loss: 0.1980 - val_accuracy: 0.9333
Epoch 288/300
67/67 [==============================] - 0s 4ms/step - loss: 0.1753 - accuracy: 0.9430 - val_loss: 0.1954 - val_accuracy: 0.9356
Epoch 289/300
67/67 [==============================] - 0s 4ms/step - loss: 0.1823 - accuracy: 0.9405 - val_loss: 0.1957 - val_accuracy: 0.9378
Epoch 290/300
67/67 [==============================] - 0s 4ms/step - loss: 0.1761 - accuracy: 0.9434 - val_loss: 0.1942 - val_accuracy: 0.9356
Epoch 291/300
67/67 [==============================] - 0s 4ms/step - loss: 0.1772 - accuracy: 0.9421 - val_loss: 0.1973 - val_accuracy: 0.9311
Epoch 292/300
67/67 [==============================] - 0s 4ms/step - loss: 0.1739 - accuracy: 0.9435 - val_loss: 0.1929 - val_accuracy: 0.9356
Epoch 293/300
67/67 [==============================] - 0s 4ms/step - loss: 0.1775 - accuracy: 0.9414 - val_loss: 0.1961 - val_accuracy: 0.9356
Epoch 294/300

KerasClassifier(
	model=None
	build_fn=<function create_neural_network_1 at 0x000002644949C820>
	warm_start=False
	random_state=None
	optimizer=rmsprop
	loss=None
	metrics=None
	batch_size=None
	validation_batch_size=None
	verbose=1
	callbacks=None
	validation_split=0.0
	shuffle=True
	run_eagerly=False
	epochs=1
	class_weight=None
)

### Train on full dataset

In [138]:
lr_scheduler = LearningRateScheduler(decay_schedule)
estimator_1 = KerasClassifier(build_fn=create_neural_network_1)
estimator_1.fit(X_train, y_train, epochs=300, batch_size=128, callbacks=[lr_scheduler])

Epoch 1/300


C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:301: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  warnings.warn(


71/71 [==============================] - 1s 5ms/step - loss: 9.1228 - accuracy: 0.4063
Epoch 2/300
71/71 [==============================] - 0s 4ms/step - loss: 5.2757 - accuracy: 0.7449
Epoch 3/300
71/71 [==============================] - 0s 4ms/step - loss: 3.0690 - accuracy: 0.8177
Epoch 4/300
71/71 [==============================] - 0s 4ms/step - loss: 1.9015 - accuracy: 0.8434
Epoch 5/300
71/71 [==============================] - 0s 4ms/step - loss: 1.4508 - accuracy: 0.8619
Epoch 6/300
71/71 [==============================] - 0s 4ms/step - loss: 1.1753 - accuracy: 0.8701
Epoch 7/300
71/71 [==============================] - 0s 4ms/step - loss: 0.9980 - accuracy: 0.8801
Epoch 8/300
71/71 [==============================] - 0s 4ms/step - loss: 0.9086 - accuracy: 0.8859
Epoch 9/300
71/71 [==============================] - 0s 4ms/step - loss: 0.8589 - accuracy: 0.8896
Epoch 10/300
71/71 [==============================] - 0s 4ms/step - loss: 0.8259 - accuracy: 0.8914
Epoch 11/300
71/71 [=

71/71 [==============================] - 0s 4ms/step - loss: 0.1610 - accuracy: 0.9470
Epoch 165/300
71/71 [==============================] - 0s 4ms/step - loss: 0.1714 - accuracy: 0.9447
Epoch 166/300
71/71 [==============================] - 0s 4ms/step - loss: 0.1629 - accuracy: 0.9467
Epoch 167/300
71/71 [==============================] - 0s 4ms/step - loss: 0.1648 - accuracy: 0.9450
Epoch 168/300
71/71 [==============================] - 0s 4ms/step - loss: 0.1689 - accuracy: 0.9449
Epoch 169/300
71/71 [==============================] - 0s 4ms/step - loss: 0.1671 - accuracy: 0.9423
Epoch 170/300
71/71 [==============================] - 0s 4ms/step - loss: 0.1661 - accuracy: 0.9449
Epoch 171/300
71/71 [==============================] - 0s 4ms/step - loss: 0.1613 - accuracy: 0.9447
Epoch 172/300
71/71 [==============================] - 0s 4ms/step - loss: 0.1697 - accuracy: 0.9393
Epoch 173/300
71/71 [==============================] - 0s 4ms/step - loss: 0.1703 - accuracy: 0.9418
Epoc

KerasClassifier(
	model=None
	build_fn=<function create_neural_network_1 at 0x0000017C552E6550>
	warm_start=False
	random_state=None
	optimizer=rmsprop
	loss=None
	metrics=None
	batch_size=None
	validation_batch_size=None
	verbose=1
	callbacks=None
	validation_split=0.0
	shuffle=True
	run_eagerly=False
	epochs=1
	class_weight=None
)

In [139]:
preds = estimator_1.predict(X_test)
preds

157/157 [==============================] - 0s 1ms/step


array([[0, 0, 1, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       ...,
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [1, 0, 0, ..., 0, 0, 0]])

In [140]:
preds_as_array = np.argmax(preds, axis=1)
preds_as_array += 1
preds_as_array

array([3, 4, 5, ..., 4, 5, 1], dtype=int64)

In [141]:
sub = make_submission(preds_as_array)
sub

C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from p

C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from p

C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from p

C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from p

C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from p

C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from p

C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  submission = submission.append({'id': label, 'class': pred}, ignore_index=True)
C:\Users\Sergiu\AppData\Local\Temp\ipykernel_11408\2162223925.py:11: FutureWarning: The frame.append method is deprecated and will be removed from p

id class
0     10001     3
1     10002     4
2     10004     5
3     10008    20
4     10009    17
...     ...   ...
4995  23986    19
4996  23991    12
4997  23992     4
4998  23998     5
4999  24000     1

[5000 rows x 2 columns]

In [142]:
sub.to_csv('submission_keras_1depth_300e_128bs_64f_std.csv', index=False)

# CNN

In [23]:
def create_cnn(num_columns=75, num_labels=20, dropout_rates=0.1, learning_rate=1e-3):
    inp = Input(shape=(num_columns,))
    x = BatchNormalization()(inp)
    x = Dropout(dropout_rates)(x)
    x = WeightNormalization(Dense(4096))(x)
    x = Reshape((256, 16))(x)
    x = BatchNormalization()(x)
    x = Dropout(0.1)(x)
    x = WeightNormalization(Conv1D(filters = 16, kernel_size = 5, activation = 'tanh', use_bias = False, padding = 'SAME'))(x)
    x = AveragePooling1D(pool_size = 2)(x)
    xs = x
    x = BatchNormalization()(x)
    x = Dropout(0.1)(x)
    x = WeightNormalization(Conv1D(filters = 16, kernel_size = 3, activation = 'tanh', use_bias = True, padding = 'SAME'))(x)
    x = BatchNormalization()(x)
    x = Dropout(0.1)(x)
    x = WeightNormalization(Conv1D(filters = 16, kernel_size = 3, activation = 'tanh', use_bias = True, padding = 'SAME'))(x)
    x = Multiply()([x, xs])
    x = MaxPool1D(pool_size = 4, strides = 2)(x)
    x = Flatten()(x)
    x = BatchNormalization()(x)
    x = Activation('relu')(x)
    x = Dense(num_labels)(x)
    out = Activation('softmax')(x)
    model = tf.keras.Model(inputs=inp, outputs=out)
    model.compile(loss='categorical_crossentropy', optimizer='adamax', metrics=['accuracy'])
    model.summary()
    return model

In [164]:
estimator_cnn = KerasClassifier(build_fn=create_cnn)

In [171]:
def step_decay(epoch):
    initial_lrate = 0.0001
    drop = 1
    epochs_drop = 10.0
    lrate = initial_lrate * math.pow(drop, math.floor((1+epoch)/epochs_drop))
    return lrate

def lr_exp_decay(epoch, lr):
    k = 10
    return initial_learning_rate * math.exp(-k*epoch)

- Adagrad, epcohs 300, bs 128, val_loss = 0.20 ish
- Adam, epochs 30, bs 128, val_loss = 0.22 ish
- Adamax, epochs 30, bs 128, val_loss = 0.20

In [172]:
lr_scheduler = LearningRateScheduler(lr_exp_decay)
estimator_cnn.fit(X_train, y_train, validation_split=0.05, epochs=30, batch_size=128, callbacks=[lr_scheduler])

Model: "model_35"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 input_47 (InputLayer)          [(None, 75)]         0           []                               
                                                                                                  
 batch_normalization_208 (Batch  (None, 75)          300         ['input_47[0][0]']               
 Normalization)                                                                                   
                                                                                                  
 dropout_170 (Dropout)          (None, 75)           0           ['batch_normalization_208[0][0]']
                                                                                                  
 weight_normalization_167 (Weig  (None, 4096)        626689      ['dropout_170[0][0]']     

C:\Users\Sergiu\.conda\envs\tf\lib\site-packages\scikeras\wrappers.py:301: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  warnings.warn(


67/67 [==============================] - 2s 13ms/step - loss: 1.1855 - accuracy: 0.6719 - val_loss: 1.0689 - val_accuracy: 0.8289
Epoch 2/30
67/67 [==============================] - 0s 6ms/step - loss: 0.5931 - accuracy: 0.8320 - val_loss: 0.7163 - val_accuracy: 0.8644
Epoch 3/30
67/67 [==============================] - 0s 6ms/step - loss: 0.4374 - accuracy: 0.8759 - val_loss: 0.4890 - val_accuracy: 0.8933
Epoch 4/30
67/67 [==============================] - 0s 6ms/step - loss: 0.3633 - accuracy: 0.8909 - val_loss: 0.3677 - val_accuracy: 0.8978
Epoch 5/30
67/67 [==============================] - 0s 6ms/step - loss: 0.3020 - accuracy: 0.9105 - val_loss: 0.2911 - val_accuracy: 0.9178
Epoch 6/30
67/67 [==============================] - 0s 6ms/step - loss: 0.2655 - accuracy: 0.9172 - val_loss: 0.2648 - val_accuracy: 0.9200
Epoch 7/30
67/67 [==============================] - 0s 6ms/step - loss: 0.2380 - accuracy: 0.9243 - val_loss: 0.2559 - val_accuracy: 0.9244
Epoch 8/30
67/67 [============

KerasClassifier(
	model=None
	build_fn=<function create_cnn at 0x0000026449113A60>
	warm_start=False
	random_state=None
	optimizer=rmsprop
	loss=None
	metrics=None
	batch_size=None
	validation_batch_size=None
	verbose=1
	callbacks=None
	validation_split=0.0
	shuffle=True
	run_eagerly=False
	epochs=1
	class_weight=None
)

### Train on full dataset

In [ ]:
lr_scheduler = LearningRateScheduler(lr_exp_decay)
estimator_cnn = KerasClassifier(build_fn=create_cnn)
estimator_cnn.fit(X_train, y_train, epochs=30, batch_size=128, callbacks=[lr_scheduler])

In [ ]:
preds = estimator_cnn.predict(X_test)
preds

In [ ]:
preds_as_array = np.argmax(preds, axis=1)
preds_as_array += 1
preds_as_array

In [ ]:
sub = make_submission(preds_as_array)
sub

In [ ]:
sub.to_csv('submission_keras_cnn_30e_128bs_75f_std.csv', index=False)

# Keras Ensemble

In [25]:
cnn = KerasClassifier(build_fn=create_cnn)
cnn._estimator_type = "classifier"

dnn = estimator_1 = KerasClassifier(build_fn=create_neural_network_1)
dnn._estimator_type = "classifier"

estimators = [("dnn", dnn), ("cnn", cnn)]
ensemble_estimators = StackingClassifier(estimators, final_estimator=LogisticRegression(), n_jobs=-1)

In [ ]:
%%time
ensemble_estimators.fit(X_train, y_train)

In [ ]:
%%time
results_list = []
estimator_list = []
cv = KFold(n_splits=5)

for estimator_name, clf in estimators:
    results = cross_val_score(clf, X_train, y_train, scoring='accuracy', cv=cv, n_jobs=-1)
    estimator_list.append(estimator_name)
    results_list.append(results)
    
    print('>%s %.3f (%.3f)' % (estimator_name, np.mean(results), np.std(results)))